In [1]:
# Imports
import numpy as np
import mdtraj as md
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import random

In [2]:
# Convenience functions
def sin(x):
    return np.sin(x)

def cos(x):
    return np.cos(x)

def sqrt(x):
    return np.sqrt(x)

pi = np.pi

In [3]:
# Define the triply periodic minimal surface functions
def SchwarzD(X, period):

    N = 2*pi/period
    
    a = sin(N*X[0]) * sin(N*X[1]) * sin(N*X[2])
    b = sin(N*X[0]) * cos(N*X[1]) * cos(N*X[2])
    c = cos(N*X[0]) * sin(N*X[1]) * cos(N*X[2])
    d = cos(N*X[0]) * cos(N*X[1]) * sin(N*X[2])
    
    return a + b + c + d

def Gyroid(X,period):
    
    N = 2*pi/period
    
    a = sin(N*X[0]) * cos(N*X[1])
    b = sin(N*X[1]) * cos(N*X[2])
    c = sin(N*X[2]) * cos(N*X[0])
    
    return a + b + c

def SchwarzD_grad(v,period):
    
    x = v[0]; y = v[1]; z = v[2]
    N = 2*pi / period
    
    a = N*cos(N*x)*sin(N*y)*sin(N*z) + N*cos(N*x)*cos(N*y)*cos(N*z) - N*sin(N*x)*sin(N*y)*cos(N*z) - N*sin(N*x)*cos(N*y)*sin(N*z)
    b = N*sin(N*x)*cos(N*y)*sin(N*z) - N*sin(N*x)*sin(N*y)*cos(N*z) + N*cos(N*x)*cos(N*y)*cos(N*z) - N*cos(N*x)*sin(N*y)*sin(N*z)
    c = N*sin(N*x)*sin(N*y)*cos(N*z) - N*sin(N*x)*cos(N*y)*sin(N*z) - N*cos(N*x)*sin(N*y)*sin(N*z) + N*cos(N*x)*cos(N*y)*cos(N*z)
    
    return np.array([a,b,c]) / np.linalg.norm(np.array([a,b,c]))

def Gyroid_grad(v,period):
    
    x = v[0]; y = v[1]; z = v[2]
    N = 2*pi / period
    
    a =  N*cos(N*x)*cos(N*y) - N*sin(N*x)*sin(N*z)
    b = -N*sin(N*y)*sin(N*x) + N*cos(N*y)*cos(N*z)
    c = -N*sin(N*y)*sin(N*z) + N*cos(N*z)*cos(N*x)
    
    return np.array([a,b,c]) / np.linalg.norm(np.array([a,b,c]))

In [22]:
# Find monomer placements
exp_unit_cell = 9.4                        # nm
exp_density = 1.1                          # g/cm^3
exp_porosity = 0.2                         # vol glycerol/vol bulk
exp_weight_pct = 0.8                       # mass monomer/mass bulk
monomer_MW = 12.01*48 + 1.008*84 + 14.01*4 # g/mol
print(monomer_MW)
n_monomer = 6.022*10**23 / monomer_MW * exp_weight_pct * exp_density / 10**21 * exp_unit_cell**3 
n_monomer = round(n_monomer)

print('%d monomers can fit in a %.1f unit cell' %(n_monomer,exp_unit_cell))
print('%d monomers can fit on one side of BCC'  %(n_monomer/2))
print('%d monomers can fit on one piece of BCC' %(n_monomer/6))

n = 100
box = exp_unit_cell * 10
period = box
x = np.linspace(0,    box, n)
y = np.linspace(0,    box, n)
z = np.linspace(0,    box, n)
X = [x[:,None,None], y[None,:,None], z[None,None,:]]

print('Box size is\t %.4f' %(box))
print('Period is\t %.4f' %(period))

#C = SchwarzD(X, period)
C = Gyroid(X, period)

grid = np.zeros([n**3, 3])
count = 0
for i in range(n):
    for j in range(n):
        for k in range(n):
            if -0.01 < C[i,j,k] < 0.01:
                grid[count,:] = [x[i], y[j], z[k]]
                count += 1
                
structure = grid[:count, :]

count = 0
monomer_placement = np.zeros([round(n_monomer),3])

while count < n_monomer/2:
    placement = random.randint(0, structure.shape[0] - 1)
    monomer_placement[count,:] = structure[placement,:]
    count += 1

#df = pd.DataFrame(monomer_placement, columns=['x','y','z'])
#df['size'] = np.ones(monomer_placement.shape[0]) * 0.1
df = pd.DataFrame(structure, columns=['x','y','z'])
df['size'] = np.ones(structure.shape[0]) * 0.1
fig = px.scatter_3d(df,x='x',y='y',z='z', opacity=1, size='size')
fig.show()

717.192
614 monomers can fit in a 9.4 unit cell
307 monomers can fit on one side of BCC
102 monomers can fit on one piece of BCC
Box size is	 94.0000
Period is	 94.0000


<img src='alignment.png'>

In [23]:
# Functions for monomer movement
def Rvect2vect(A, B):
    a = A / np.linalg.norm(A) # to be rotated
    b = B / np.linalg.norm(B) # to rotate to
    
    v = np.cross(a,b)
    s = np.linalg.norm(v)
    c = np.dot(a,b)
    
    v_skew = np.array([[    0, -v[2],  v[1]], 
                       [ v[2],     0, -v[0]],
                       [-v[1],  v[0],    0]])
    
    R = np.identity(3) + v_skew + np.dot(v_skew,v_skew) * (1 - c)/s**2
   
    return np.array(R)

def rotate_coords(coords, R):
    
    pos = np.copy(coords)
    for i in range(np.shape(coords)[0]):
        pos[i,:] = np.dot(R,pos[i,:])
        
    return pos

def translate(coords, from_loc, to_loc):
    
    pos = np.copy(coords)
    direction = to_loc - from_loc
    
    T = np.array([[1,0,0,direction[0]],
                  [0,1,0,direction[1]],
                  [0,0,1,direction[2]],
                  [0,0,0,1           ]])
    
    b = np.ones([1])
    for i in range(pos.shape[0]):
        P = np.concatenate((pos[i,:], b))
        x = np.dot(T,P)
        pos[i,:] = x[:3]
        
    return pos

def get_reference_point(coords, topology, ref_groups):
    
    ref_point = np.zeros([1,3])
    for name in ref_groups:
        ref_idx = topology[topology.name == name].index[0]
        ref_point += coords[ref_idx,:]
        
    ref_point = ref_point[0] / len(ref_groups)
    
    return ref_point

def get_monomer_info(PDB_file):
    
    monomerPDB = md.formats.PDBTrajectoryFile(PDB_file)
    monomerArray = monomerPDB.positions[0,:,:]
    atoms_per_monomer = monomerArray.shape[0]
    top, _ = monomerPDB.topology.to_dataframe()

    return monomerArray, atoms_per_monomer, top
    
def get_monomer_vector(coords, topology, ref_head_groups, ref_tail_groups):
    
    vector_head = np.zeros([1,3])
    for name in ref_head_groups:
        head_idx = topology[topology.name == name].index[0]
        vector_head += coords[head_idx,:]
    
    vector_head = vector_head[0] / len(ref_head_groups)

    vector_tail = np.zeros([1,3])
    for name in ref_tail_groups:
        tail_idx = topology[topology.name == name].index[0]
        vector_tail += coords[tail_idx,:]
    
    vector_tail = vector_tail[0] / len(ref_tail_groups)
    monomer_vector = vector_head - vector_tail

    return monomer_vector

In [24]:
shift = 10
struct = 'Gyroid'

ref_head_groups = ['C18','C19','N','N1','C47','C26','C27','N2','N3','C46']
ref_tail_groups = ['C','C1','C44','C45']
monomerArray, atoms_per_monomer, topology = get_monomer_info('./Dibrpyr14.pdb')
ref_point = get_reference_point(monomerArray, topology, ref_head_groups)

total_atoms = round(n_monomer/2 * atoms_per_monomer)
monolayer1 = np.zeros([total_atoms,3])

for i in range(round(n_monomer/2)):
    
    # Calculate the gradient at new position
    if struct == 'SchwarzD':
        n = SchwarzD_grad(monomer_placement[i,:], period)
    elif struct == 'Gyroid':
        n = Gyroid_grad(monomer_placement[i,:], period)
    else:
        raise NameError('Not a valid structure name. Try: SchwarzD or Gyroid')
    
    
    # Translate the monomer to the origin
    origin_positions = translate(monomerArray, ref_point, [0,0,0])
    monomer_vector = get_monomer_vector(origin_positions, topology, ref_head_groups, ref_tail_groups)
    
    # Rotate the monomer for new position
    R = Rvect2vect(monomer_vector, n)
    rotated_positions = rotate_coords(origin_positions, R)
    ref_point = get_reference_point(rotated_positions, topology, ref_head_groups)
    
    # Shift the placement along the interface
    shifted_placement = monomer_placement[i,:] - shift*n
    
    # Translate the monomer to new position
    translated_positions = translate(rotated_positions, ref_point, shifted_placement)
    
    # Save the new coordinates
    monolayer1[atoms_per_monomer*i:atoms_per_monomer*(i+1)] = translated_positions

    
# Place on other side of BCC
monolayer2 = np.zeros([total_atoms,3])
for i in range(round(n_monomer/2)):
    
    # Calculate the gradient at new position
    if struct == 'SchwarzD':
        n = -SchwarzD_grad(monomer_placement[i,:], period)
    elif struct == 'Gyroid':
        n = -Gyroid_grad(monomer_placement[i,:], period)
    else:
        raise NameError('Not a valid structure name. Try: SchwarzD or Gyroid')
    
    # Translate the monomer to the origin
    origin_positions = translate(monomerArray, ref_point, [0,0,0])
    monomer_vector = get_monomer_vector(origin_positions, topology, ref_head_groups, ref_tail_groups)
    
    # Rotate the monomer for new position
    R = Rvect2vect(monomer_vector, n)
    rotated_positions = rotate_coords(origin_positions, R)
    ref_point = get_reference_point(rotated_positions, topology, ref_head_groups)
    
    # Shift the placement along the interface
    shifted_placement = monomer_placement[i,:] - shift*n
    
    # Translate the monomer to new position
    translated_positions = translate(rotated_positions, ref_point, shifted_placement)
    
    # Save the new coordinates
    monolayer2[atoms_per_monomer*i:atoms_per_monomer*(i+1)] = translated_positions

In [25]:
n_plot = 100
bilayer = np.concatenate((monolayer1, monolayer2))
df3 = pd.DataFrame(bilayer,columns=['x','y','z'])
df3['size'] = np.ones(df3.shape[0])

fig = px.scatter_3d(df,x='x',y='y',z='z', opacity=1, size='size')
fig.add_trace(
    go.Scatter3d(
        x=df3.head(n_plot*atoms_per_monomer).x,
        y=df3.head(n_plot*atoms_per_monomer).y,
        z=df3.head(n_plot*atoms_per_monomer).z,
        mode='markers', marker=dict(size=1, line=dict(color='white')),
        name='outside'
    ))
fig.add_trace(
    go.Scatter3d(
        x=df3.tail(n_plot*atoms_per_monomer).x,
        y=df3.tail(n_plot*atoms_per_monomer).y,
        z=df3.tail(n_plot*atoms_per_monomer).z,
        mode='markers', marker=dict(size=1, line=dict(color='white')),
        name='inside'
    ))

fig.show()